In [45]:
import itertools
import random
import numpy as np
import pandas as pd
import random
import matplotlib.pyplot as plt

class TaxiEnvironment:
    def __init__(self, customers_info,start=(3,1)):
        self.grid_size = 5
        self.customers_info = customers_info
        self.hazardous = [(0,2),(1,2),(2,2)]
        self.discount_factor = 0.9
        self.initial_prob = 0.8
        self.pickup_prob = 0.9
        self.pickedup=[]
        self.premium_preference = 0
        self.start = start
        self.pickups = [i[0] for i in customers_info]
        self.is_different_customers = any(x[1] for x in customers_info) and any(not x[1] for x in customers_info)
        self.values = self.value_iteration()
        self.policy = self.extract_policy(self.values)
        print("Pick Up points : ",self.pickups)
        self.display_grid()
    def get_states(self):
        taxi_positions = [(taxi_x, taxi_y) for taxi_x in range(self.grid_size) for taxi_y in range(self.grid_size)]
        return taxi_positions

    def get_actions(self):
        return [(0, 1), (0, -1), (1, 0), (-1, 0)]  # Right, Left, Down, Up

    def is_valid_position(self, position):
        return 0 <= position[0] < self.grid_size and 0 <= position[1] < self.grid_size

    def get_reward(self, current_state):
        taxi_position = current_state
        customer_position=self.customers_info
        reward = -0.1
        for customer_position, is_premium in self.customers_info:
            if taxi_position == customer_position:
                if is_premium and len(self.pickedup)==0:
                  self.premium_preference+=1
                self.pickedup.append(taxi_position)
                reward += 30 if is_premium else 20

        # Check for hazardours areas
        if taxi_position in self.hazardous:
            reward -= 10

        return reward

    def Trans_Prob(self,state,action,values):
      next_value = 0
      next_taxi_position = (state[0] + action[0], state[1] + action[1])
      actions = [(0, 1), (0, -1), (1, 0), (-1, 0)]  # Right, Left, Down, Up
      # Ensure the next position stays within the grid boundaries
      next_taxi_position = (max(0, min(next_taxi_position[0], self.grid_size - 1)),max(0, min(next_taxi_position[1], self.grid_size - 1)))
      # Check for opposite direction movement
      if action != (0, 0) and (action[0] != -state[0] or action[1] != -state[1]):
        next_state = next_taxi_position
        reward = self.get_reward(next_state)
        next_value = reward + self.discount_factor * values[next_state]
       # Adjust probability based on pickup
        prob = self.pickup_prob if reward > 0 else self.initial_prob
        # Stochasticity: Adjusted probability of going in the intended direction
        for random_action in actions:
          if random_action != action:
            next_taxi_position_random = (state[0] + random_action[0],state[1] + random_action[1])
          # Ensure the random position stays within the grid boundaries
            next_taxi_position_random = (max(0, min(next_taxi_position_random[0], self.grid_size - 1)),max(0, min(next_taxi_position_random[1], self.grid_size - 1)))
            next_state_random = next_taxi_position_random
            reward_random = self.get_reward(next_state_random)
            value_random = reward_random + self.discount_factor * values[next_state_random]
            next_value += prob * (value_random - next_value)
      return next_value
    def value_iteration(self, epsilon=1e-7):
        states = self.get_states()
        actions = [(0, 1), (0, -1), (1, 0), (-1, 0)]  # Right, Left, Down, Up
        max_iterations = 500
        # Initialize values arbitrarily
        values = {state: 0 for state in states}
        k=0
        while True:
            delta = 0
            for state in states:
                current_value = values[state]
                max_value = float('-inf')

                # Iterate over possible actions
                for action in actions:
                  next_value = self.Trans_Prob(state,action,values)
                  max_value = max(max_value, next_value)

                values[state] = max_value
                delta = max(delta, abs(current_value - max_value))
            k+=1
            if delta < epsilon :
                break

        return values

    def extract_policy(self, values):
        policy = {}
        actions = self.get_actions()

        for state in values:
            taxi_position = state
            customers_info=self.customers_info.copy()

            reward = 0
            for customer_position, is_premium in customers_info:
                if taxi_position == customer_position:
                    reward += 30 if is_premium else 20

            # Check for Hazardous zones
            if taxi_position in self.hazardous:
                reward -= 10

            if reward > 0:
                continue  # Taxi already at a customer, no need to move

            max_action = None
            max_value = float('-inf')

            for action in actions:
                next_taxi_position = (taxi_position[0] + action[0], taxi_position[1] + action[1])

                # Ensure the next position stays within the grid boundaries
                next_taxi_position = (
                    max(0, min(next_taxi_position[0], self.grid_size - 1)),
                    max(0, min(next_taxi_position[1], self.grid_size - 1))
                )

                # Check for opposite direction movement
                if action != (0, 0) and (
                        action[0] != -taxi_position[0] or action[1] != -taxi_position[1]):
                    next_state = next_taxi_position
                    customers_info=self.customers_info
                    reward = self.get_reward(next_state)
                    next_value = reward + self.discount_factor * values[next_state]

                    # Adjust probability based on pickup
                    prob = self.pickup_prob if reward > 0 else self.initial_prob

                    # Stochasticity: Adjusted probability of going in the intended direction
                    for random_action in actions:
                        if random_action != action:
                            next_taxi_position_random = (
                                taxi_position[0] + random_action[0],
                                taxi_position[1] + random_action[1]
                            )

                            # Ensure the random position stays within the grid boundaries
                            next_taxi_position_random = (
                                max(0, min(next_taxi_position_random[0], self.grid_size - 1)),
                                max(0, min(next_taxi_position_random[1], self.grid_size - 1))
                            )

                            next_state_random = next_taxi_position_random
                            reward_random = self.get_reward(next_state_random)
                            value_random = reward_random + self.discount_factor * values[next_state_random]

                            next_value += prob * (value_random - next_value)

                    if next_value > max_value:
                        max_value = next_value
                        max_action = action

            policy[state] = max_value

        return policy

    def display_grid (self):
      grid = [['' for _ in range(self.grid_size)] for _ in range(self.grid_size)]
      for state, action in self.values.items():
        grid[state[0]][state[1]]=action
      grid[self.start[0]][self.start[1]]="   Taxi   "
      k=1
      self.pickedup=set(self.pickedup)
      print(self.pickedup,"pickedup")
      for i in self.pickedup:
        grid[i[0]][i[1]]="  Pickup"+str(k)+"  "
        k+=1
      df = pd.DataFrame(grid)
      styles = [
            dict(selector="th", props=[("border", "1px solid #cccccc")]),
            dict(selector="td", props=[("border", "1px solid #cccccc")]),
        ]
      display(df.style.set_table_styles(styles))

def random_customers():
    start_position_r4 = random.choice([(i, j) for i in range(5) for j in range(5) if (i, j) not in [(0,2),(1,2),(2,2)]])
    # Generate first customer request
    customer_a_r4 = (random.choice([i for i in [(0,1),(0,3),(4,0),(4,4)] if i != start_position_r4]),False)
    # Decide whether to generate a second request
    if random.random() <= 0.6:
      # Generate second customer request at a different location
      customer_b_r4 = (random.choice([i for i in [(0,1),(0,3),(4,0),(4,4)] if (i != customer_a_r4[0] and i !=start_position_r4)]),False)
      # Decide whether one of the requests is from a premium customer
      if random.random() <= 0.3:
        # Make one of the requests from a premium customer
        premium_customer_choice = random.choice([customer_a_r4, customer_b_r4])
        premium_customer_choice = (premium_customer_choice[0], True)
        if premium_customer_choice[0] == customer_a_r4[0]:
          customer_a_r4 = premium_customer_choice
        else:
          customer_b_r4 = premium_customer_choice
    else:
      customer_b_r4 = None

    return customer_a_r4, customer_b_r4, start_position_r4


**R1: The agent should pick up a regular customer from position A. In this scenario only one customer has made a request to the agent. The taxi starts in position (2,2). To demonstrate that your code is working, produce the optimal policy**

In [46]:
#R1  -> Regular customer at pick up pint A (0,1)

taxi_env = TaxiEnvironment(customers_info=[((0,1), False)])

Pick Up points :  [(0, 1)]
{(0, 1)} pickedup


**R2: The agent should pick up a premium customer from position B. In this scenario only one customer has made a request to the agent**

In [47]:
#R2 -> Premium customer at pick up point B (0,3)
print("R2 -> Optimal Policy for premium customer at (0,3) :\n")
taxi_env = TaxiEnvironment( customers_info=[((0,3), True)])

R2 -> Optimal Policy for premium customer at (0,3) :

Pick Up points :  [(0, 3)]
{(0, 3)} pickedup


**R3: The agent should pick up a premium customer from position B. In this
scenario two customers have made requests to the agent, a regular customer at point A and a premium customer at position B**

In [48]:

#R3 -> Regular customer at pickup point A (0,1) and  Premium customer at pick up point B (0,3)
print("R3 -> Optimal Policy for regular  customer at (0,1) and premium customer at (0,3):\n")
taxi_env = TaxiEnvironment( customers_info=[((0,1), False),((0,3), True)])

R3 -> Optimal Policy for regular  customer at (0,1) and premium customer at (0,3):

Pick Up points :  [(0, 1), (0, 3)]
{(0, 1), (0, 3)} pickedup


**R4: Run 1000 episodes with random locations of customers. At any given  episode, a customer request originating at any of the 4 pickup points is
generated at random. A further request (at a point also chosen at random but different from the first chosen point) may happen with probability 0.6. When two requests are received, one of these two (randomly chosen) requests happen to be from a premium customer with probability 0.3. The taxi position should also be chosen randomly from any location in the grid except for position R**

In [49]:
# R4: Run 1000 episodes with random locations of customers
premium_preference_count = 0
for episode in range(1000):
  customer_a_r4, customer_b_r4,start_position_r4 = random_customers()
  customers_info =[]
  customers_info.append(customer_a_r4)
  if customer_b_r4:
    customers_info.append(customer_b_r4)
  print(f"\nR4 -> Optimal Policy for episode - {episode+1}:")
  env_r4= TaxiEnvironment(customers_info,start_position_r4)
  premium_preference_count += env_r4.premium_preference
  print()


R4 -> Optimal Policy for episode - 1:
Pick Up points :  [(4, 4)]
{(4, 4)} pickedup




R4 -> Optimal Policy for episode - 2:
Pick Up points :  [(4, 4), (0, 1)]
{(0, 1), (4, 4)} pickedup




R4 -> Optimal Policy for episode - 3:
Pick Up points :  [(0, 1), (4, 0)]
{(0, 1), (4, 0)} pickedup




R4 -> Optimal Policy for episode - 4:
Pick Up points :  [(4, 0), (0, 1)]
{(0, 1), (4, 0)} pickedup




R4 -> Optimal Policy for episode - 5:
Pick Up points :  [(0, 1)]
{(0, 1)} pickedup


...



R4 -> Optimal Policy for episode - 996:
Pick Up points :  [(4, 4)]
{(4, 4)} pickedup




R4 -> Optimal Policy for episode - 997:
Pick Up points :  [(0, 1)]
{(0, 1)} pickedup




R4 -> Optimal Policy for episode - 998:
Pick Up points :  [(4, 0)]
{(4, 0)} pickedup




R4 -> Optimal Policy for episode - 999:
Pick Up points :  [(0, 3), (4, 0)]
{(4, 0), (0, 3)} pickedup




R4 -> Optimal Policy for episode - 1000:
Pick Up points :  [(0, 1)]
{(0, 1)} pickedup


**Compute the fraction of the time that the agent prefers the premium customer over the regular customers over those episodes where both types of customers have made requests for pickup**

In [50]:
# Compute the fraction of the time that the agent prefers the premium customer
premium_preference_fraction = premium_preference_count / 1000
print(f"Premium Preference Fraction (R4): {premium_preference_fraction:.2%}")

Premium Preference Fraction (R4): 10.10%
